In [2]:
from matplotlib import pyplot as plt
import numpy as np
import h5py 
import yaml
import datetime
import os
import h5py
from tqdm import tqdm
from sklearn.decomposition import PCA
import json

datadir = '/global/cfs/projectdirs/dune/www/data/LBL/SingleCube/Nov2023/ramp/'
configdir = '/global/cfs/projectdirs/dune/www/data/LBL/SingleCube/Nov2023/asic_configs/'

def get_list_of_h5_files(file_or_dir_name):
    if os.path.isfile(file_or_dir_name):
        return [file_or_dir_name]
    else:
        base = file_or_dir_name
        sorted_files = [base + "/" + name for name in os.listdir(base) if (name[-3:] == ".h5")]
        sorted_files.sort(key=lambda x: os.path.getmtime(x))
        return sorted_files

# CONSTRUCT Geometry Information for Charge

nonrouted_channels=[6,7,8,9,22,23,24,25,38,39,40,54,55,56,57]
routed_channels=[i for i in range(64) if i not in nonrouted_channels]

geo=None
geometrypath = 'layout-2.4.0.yaml'
with open(geometrypath) as fi:
    geo=yaml.full_load(fi)

chip_pix=dict([(chip_id, pix) for chip_id,pix in geo['chips']])

N_CHIPS=100
N_CHANNELS=64
all_uniques = np.zeros( N_CHIPS*N_CHANNELS )
pixel_x     = np.zeros( N_CHIPS*N_CHANNELS )
pixel_y     = np.zeros( N_CHIPS*N_CHANNELS )

def chip_channel_to_index(chip, channel):
    return (chip-11)*N_CHANNELS + channel

counter_used = set()

for chip in range(11, 111):
    for channel in range(64):
        pix=chip_pix[chip][channel]
        counter = chip_channel_to_index(chip, channel)
        if not pix is None:
            pixel_x[counter] = geo['pixels'][pix][1]
            pixel_y[counter] = geo['pixels'][pix][2]

#Construct Light Geometry

light_channels = [30, 20, 18, 16, 14, 12, 4, 2, 0, 62, 52, 50, 48, 46, 44, 32]
light_channel_index = np.ones(N_CHANNELS)*-1

for ich, channel in enumerate(light_channels):
    light_channel_index[channel] = ich

#Gives TOP to BOTTOM numbering of channels
light_channel_index = light_channel_index.astype(int)

In [3]:
sync_packet_type = 6
vd = 0.016 #cm/clock cycle

def packets_to_full_timestamp(packets):
    syncs = np.where(packets['packet_type']==6)[0]
    correction = np.zeros(len(packets))
    for i in tqdm(range(1, len(syncs))):
        correction[ syncs[i] :   ] += 1e7
    return packets['timestamp'] + correction
        
def find_events(packets, charge=True, light=True): 
    
    #get true timestamps accounting for sync
    true_timestamps = packets_to_full_timestamp(packets)
    
    no_sync_mask = true_timestamps % 1e7 > 0
    packets = packets[no_sync_mask] 
    true_timestamps = true_timestamps[no_sync_mask]
    
    dmask = np.logical_and(packets['packet_type']==0, packets['valid_parity']==1)
    
    dtime, data = true_timestamps[dmask], packets[dmask]
    
    charge_mask = data['io_channel'] <  5
    light_mask  = data['io_channel'] == 5
    
    ctime, cdata = dtime[charge_mask], data[charge_mask]
    ltime, ldata = dtime[light_mask], data[light_mask]
 
    charge_clusters = (np.ones( len(cdata)  )*-1).astype(int)
    light_clusters =  (np.ones( len(ldata)  )*-1).astype(int)
    
    ievt = 0
    
    #cluster light
    
    if light:
        used = set()
        timestamps = set(ltime)
        
        for timestamp in tqdm(timestamps):
            if timestamp in used: continue
            td = np.logical_and( ltime < timestamp+5, ltime > timestamp-5 )
        
            if np.sum(td) < 2: continue
        
            used.add(timestamp)
            used.add(timestamp-1)
            used.add(timestamp-2)
            used.add(timestamp+1)
            used.add(timestamp+2)
            used.add(timestamp+3)
            used.add(timestamp+4)
            used.add(timestamp-3)
            used.add(timestamp-4)
                
            light_clusters[td] = ievt
            ievt += 1
    
    #t0 for each light event
    evt_time = np.zeros(ievt)
    for evt in set(light_clusters):
        time = np.min( ltime[ light_clusters == evt ] )
        evt_time[evt] = time
        
    if charge and light:
        timestamps = set(ctime)
        used = ctime < 0
        for timestamp in tqdm(timestamps):
            cdiff = ctime - timestamp
            cmask = np.absolute(cdiff) < 2000
            if not np.any( np.logical_and( np.logical_not(used), cmask  ) ): continue
           
            used = np.logical_or(used, cmask)
            
            #see if any light triggers in this time
            min_time = min(ctime[cmask])
            
            l_ev_diff = -1*(evt_time - min_time)
            lmask = np.logical_and(l_ev_diff < 1000, l_ev_diff > -1000)
            
            if np.any(lmask):
                evt = np.max( np.where(lmask) )
                charge_clusters[cmask] = evt
            else:
                charge_clusters[cmask] = ievt
                ievt +=1    
    
    return dict( {
        'charge_data'     : cdata,
        'charge_time'     : ctime,
        'light_data'      : ldata,
        'light_time'      : ltime,
        'charge_clusters' : charge_clusters,
        'light_clusters'  : light_clusters,
    } )

In [4]:
def get_date_datafile(filename):
    dtime = ((filename.split('packets-')[-1]).split('.h5')[0]).split('_')
    year = int(dtime[0])
    month = int(dtime[1])
    day = int(dtime[2])
    hour = int(dtime[3])
    minute = int(dtime[4])
    second = int(dtime[5])
    return year, month, day, hour, minute, second 

def get_date_config(filename):
    dtime = (filename.split('asic_configs_')[-1]).split('_')
    year = int(dtime[0])
    month = int(dtime[1])
    day = int(dtime[2])
    hour = int(dtime[3])
    minute = int(dtime[4])
    second=0
    try:
        second = int(dtime[-1])
    except:
        second = 0
    return year, month, day, hour, minute, second 


config_dict = {}
pbar = tqdm(os.listdir(configdir))
pbar.set_description('Compiling asic configs...')
for f in pbar:
    if not os.path.isdir(configdir+f) or not ('asic_configs' in f): continue
    year, month, day, hour, minute, second  = get_date_config(f)
    
    larpixconf =   {}
    lightpixconf = {}
    
    
    bias_times = {
        '45V' : list([datetime.datetime(year=year,day=5, month=12, hour=15, minute=30),
                datetime.datetime(year=year,day=5, month=12, hour=19, minute=4)]),
        '46V' : list([datetime.datetime(year=year,day=5, month=12, hour=19, minute=4),
                 datetime.datetime(year=year, day=6, month=12, hour=23, minute=59)])  
    }
    
    HV_times = {
        '0kV' : list([datetime.datetime(year=2019,day=5, month=12, hour=15, minute=30),
                datetime.datetime(year=2023,day=5, month=12, hour=16, minute=30)]),
        '6kV' : list([datetime.datetime(year=2023,day=5, month=12, hour=16, minute=30),
                 datetime.datetime(year=2023, day=5, month=12, hour=16, minute=53)]),
        '9kV' : list([datetime.datetime(year=2023,day=5, month=12, hour=16, minute=53),
                 datetime.datetime(year=2023, day=5, month=12, hour=16, minute=57)]),
        '11kV' : list([datetime.datetime(year=2023,day=5, month=12, hour=16, minute=57),
                 datetime.datetime(year=2023, day=5, month=12, hour=17, minute=22)]),
        '13kV' : list([datetime.datetime(year=2023,day=5, month=12, hour=17, minute=22),
                 datetime.datetime(year=2023, day=5, month=12, hour=17, minute=38)]),
        '15kV' : list([datetime.datetime(year=2023,day=5, month=12, hour=18, minute=00),
                 datetime.datetime(year=2023, day=6, month=12, hour=23, minute=59)]),
    }
    
    
    HV = 'None'
    charge = 'None'
    light = 'None'

    if os.path.exists(configdir+f+'/config_1-1-11.json'):
        with open(configdir+f+'/config_1-1-11.json', 'r') as ff:
            larpixconf = json.load(ff)
        tg = larpixconf['threshold_global']
        pr = larpixconf['enable_periodic_trigger']
        
        if tg==31 and pr==0:
            charge='nominal threshold'
        elif tg==30 and pr==0:
            charge='low threshold'
        elif tg==255 and pr==1:
            charge='pedestal'
        else:
            charge='Check logbook'
            
        dt = datetime.datetime(year=year, day=day, month=month, hour=hour, minute=minute)
        for bias in HV_times:
            if dt > HV_times[bias][0] and dt < HV_times[bias][1]:
                HV = bias
        
    if os.path.exists(configdir+f+'/config_1-5-11.json'):
        with open(configdir+f+'/config_1-5-11.json', 'r') as ff:
            lightpixconf = json.load(ff)
        
        tg = lightpixconf['threshold_global']
        if tg==30:
            light='nominal threshold'
        if tg==29:
            light='low threshold'
        else:
            light='scan'
        
        dt = datetime.datetime(year=year, day=day, month=month, hour=hour, minute=minute)
        for bias in bias_times:
            if dt > bias_times[bias][0] and dt < bias_times[bias][1]:
                light += ', {}'.format(bias)
        
    config_dict[f] = {
        'year' : year,
        'month': month,
        'day'  : day,
        'hour' : hour,
        'minute':minute,
        'second':second,
        'charge' : charge,
        'light'  : light,
        'HV'     : HV
    }
    
# Loop over all files, get date, find associated asic configs
# Write dictionary with filename, date/time of asic configs, store as json file

data_dict   = {}
ifile=0
pbar = tqdm(get_list_of_h5_files(datadir))
pbar.set_description('Associating asic configs to date files...')
writedir='/global/cfs/projectdirs/dune/www/data/LBL/SingleCube/Nov2023/simple_v2/'
for file in pbar:
    year, month, day, hour, minute, second = get_date_datafile(file)
    
    timedeltas = [ datetime.timedelta( \
        days=(day-config_dict[key]['day']), 
        seconds=(second-config_dict[key]['second']),
        minutes=(minute-config_dict[key]['minute']),
        hours=(hour-config_dict[key]['hour']) \
    ) for key in config_dict.keys() ]
    
    timedeltas = [ t if t > datetime.timedelta(0.) else datetime.timedelta(999999) for t in timedeltas  ]
    
    #find associated asic config
    config  = list(config_dict.keys())[np.argmin( timedeltas )]
    data_dict[ifile] = {
        
        'filename'  : str(file),
        'simple_filename' : str(writedir + 'simple-{}'.format( file.split('packets-')[-1] )),
        'date'      : str('{}/{}/{}'.format(month, day, year)),
        'time'      : str('{}:{}:{}'.format(hour, minute, second)),
        'config'    : str('{}/{}'.format(configdir, config)),
        'charge'    : str( config_dict[config]['charge'] ),
        'light'     : str( config_dict[config]['light'] ),
        'HV'        : str( config_dict[config]['HV'] )
    }
    
    ifile += 1
    
with open('datafiles_nosync.json', 'w') as f:
    json.dump(data_dict, f, indent=4)

Associating asic configs to date files...: 100%|██████████| 663/663 [00:07<00:00, 92.16it/s]


In [4]:
def get_all_channel_mean(unique, data):
    u = np.array(list(set(unique)))
    d = np.zeros(len(u))
    iun=0
    for un in tqdm(u):
        mask = unique==un
        d[iun] = np.mean(data[mask])
        iun+=1
        
    return u, d

def get_all_channel_std(unique, data):
    u = np.array(list(set(unique)))
    d = np.zeros(len(u))
    iun=0
    for un in tqdm(u):
        mask = unique==un
        d[iun] = np.std(data[mask])
        iun+=1
        
    return u, d

def get_all_channel_count(unique, data):
    u = np.array(list(set(unique)))
    d = np.zeros(len(u))
    iun=0
    for un in tqdm(u):
        mask = unique==un
        d[iun] = np.sum(mask.astype(int))
        iun+=1
        
    return u, d
 
def display_1d(c,title=None):
    fig = plt.figure(figsize=(12, 10) )
    ax = fig.add_subplot()
    ax.hist(c, bins=50, range=(0, 100))
    ax.set_xlabel('dataword [adc]', fontsize=12)
    ax.grid()
    if not title is None: ax.set_title(title)
    plt.show()
    
def display_2d(x, y, c, title=None, cut=None):
    fig = plt.figure(figsize=(12, 10) )
    ax = fig.add_subplot()
    mask = [True]*len(c)
    if not cut is None:
        mask = c < cut
    
    sc = ax.scatter(x[mask], y[mask], c=c[mask], marker='s', s=40)
    #ax.axhline(50, color='red')

    cbar = plt.colorbar(sc, ax=ax)
    cbar.set_label('dataword', rotation=270)
    if not title is None: ax.set_title(title)
    plt.show()
    
def display_3d(x, y, z, c, title=None, view=None):
    fig = plt.figure(figsize=(12, 10) )
    ax = fig.add_subplot(projection='3d')
    sc = ax.scatter(x, y, z, c=c, marker='s', s=20, alpha=0.5)
    cbar = plt.colorbar(sc, ax=ax)
    cbar.set_label('dataword', rotation=270, fontsize=14)
    if not view is None:
        ax.view_init(*view)
    
    ax.set_xlabel('x [mm]', fontsize=12)
    ax.set_ylabel('y [mm]', fontsize=12)
    ax.set_zlabel('z (drift) [mm]', fontsize=12)
    ax.set_xlim(-150, 150)
    ax.set_ylim(-150, 150)
    #ax.set_zlim(0, 100)
    #ax.set_zlim(0, 5)
    if not title is None: ax.set_title(title)

In [5]:
def dword_to_mv(dword):
    vref = 223/256*1800.
    vcm  = 68/256*1800
    return (dword/256.)*(vref-vcm) + vcm

#Pedestal File
filename = '/global/cfs/projectdirs/dune/www/data/LBL/SingleCube/Nov2023/cold/packets-2023_12_05_14_32_11_PST.h5'
f = h5py.File(filename)
packets = f['packets']
dmask = np.logical_and(packets['packet_type']==0, packets['valid_parity']==1)
dmask = np.logical_and(dmask, packets['chip_id']<111)
data = packets[dmask]

q = data['dataword']
indices = chip_channel_to_index(data['chip_id'].astype(int), data['channel_id'].astype(int))
pedu, pedmean = get_all_channel_mean(indices, q)
peds_ind = np.zeros(100*64)
for chip in range(11, 111):
    for channel in range(64):
        counter = chip_channel_to_index(chip, channel)
        if counter in pedu:
            peds_ind[counter] = dword_to_mv(pedmean[np.where(pedu==counter)[0][0]])

100%|██████████| 4774/4774 [00:00<00:00, 16926.56it/s]


In [ ]:
import time
gain = 4.522 #mV/ke-
while True:
    try:
        for ifile in list(data_dict.keys()):
            #start=time.time()
            fname = data_dict[ifile]['simple_filename']
            if os.path.exists(fname): 
                continue
            if os.path.getsize(data_dict[ifile]['filename'])  > 5e8: continue
            f= h5py.File( data_dict[ifile]['filename'] )
            packets = f['packets']
            if len(packets) < 10:
                continue
            evs = find_events(packets)
            hf = h5py.File(fname, 'w')
            hf.create_dataset('light_ts', data=evs['light_time'])
            hf.create_dataset('charge_ts', data=evs['charge_time'])
            hf.create_dataset('charge_event', data=evs['charge_clusters'])
            hf.create_dataset('light_event', data=evs['light_clusters'])
            hf.create_dataset('charge_chipid', data=evs['charge_data']['chip_id'])
            hf.create_dataset('charge_chanid', data=evs['charge_data']['channel_id'])
    
            indices = chip_channel_to_index(evs['charge_data']['chip_id'].astype(int),
                                    evs['charge_data']['channel_id'].astype(int))
    
            hf.create_dataset('charge_q', data= (dword_to_mv(evs['charge_data']['dataword'])-peds_ind[indices])/gain )
            hf.create_dataset('charge_x', data=pixel_x[indices] )
            hf.create_dataset('charge_y', data=pixel_y[indices] )
            hf.create_dataset('light_chanid', data=evs['light_data']['channel_id'])
            hf.create_dataset('light_data', data=evs['light_data']['dataword'])
            hf.close()
    except:
        pass

4774